## RECOMMENDER TEST

**SUMMARY:**

We will be constructing a first run recommender to test our data based solely on correlation between ratings and wine.  This will help confirm that the dataframes we have assembled will be compatible when subjected to a recommender operation.  Since this will be a basic recommender, we will be limiting our input to only the key elements necessary for this exercise.

#### IMPORT PACKAGES

In [1]:
import pandas as pd
import numpy as np
from scipy import sparse
from sklearn.metrics.pairwise import pairwise_distances

#### IMPORT WINE CATALOG AND USER FILES AND PREP FOR PIVOT TABLE

In [3]:
wine = pd.read_csv('./data/wine_catalog.csv')
wine = wine.fillna("")
wine.head()

Unnamed: 0                    winery  \
0           0                    Caymus   
1           1              The Prisoner   
2           2                      Masi   
3           3  Stag's Leap Wine Cellars   
4           4                     Banfi   

                                                wine  rating  \
0                            Cabernet Sauvignon N.V.     4.6   
1                                  The Prisoner N.V.     4.4   
2  Costasera Amarone della Valpolicella Classico ...     4.3   
3                    ARTEMIS Cabernet Sauvignon N.V.     4.3   
4                        Brunello di Montalcino N.V.     4.2   

           wine_style wine_category vintage  \
0  Cabernet Sauvignon           Red    N.V.   
1               Blend           Red    N.V.   
2        Valpolicella           Red    N.V.   
3  Cabernet Sauvignon           Red    N.V.   
4            Brunello           Red    N.V.   

                                region        country  price  \
0                          Napa Valley  United States  79.05   
1                          Napa Valley  United States  39.75   
2  Amarone della Valpolicella Classico          Italy  54.99   
3                          Napa Valley  United States  59.99   
4               Brunello di Montalcino          Italy  65.98   

  contact_for_price  wine_style_code  wine_category_code  region_code  \
0                                 15                   2          587   
1                                 10                   2          587   
2                                 86                   2           34   
3                                 15                   2          587   
4                                 12                   2          120   

   country_code  
0            36  
1            36  
2            19  
3            36  
4            19

In [4]:
wine.drop(['Unnamed: 0','winery','wine_style','wine_category','vintage','region','country','price','contact_for_price','wine_style_code','wine_category_code','region_code','country_code'],axis=1,inplace=True)

In [5]:
wine.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 33163 entries, 0 to 33162
Data columns (total 2 columns):
wine      33163 non-null object
rating    33163 non-null float64
dtypes: float64(1), object(1)
memory usage: 518.3+ KB


In [6]:
wine=wine.rename(columns = {'wine':'wine_label'})
wine.head()

wine_label  rating
0                            Cabernet Sauvignon N.V.     4.6
1                                  The Prisoner N.V.     4.4
2  Costasera Amarone della Valpolicella Classico ...     4.3
3                    ARTEMIS Cabernet Sauvignon N.V.     4.3
4                        Brunello di Montalcino N.V.     4.2

In [7]:
ratings = pd.read_csv('./data/user.csv')
ratings = ratings.fillna(0.0)
ratings.head()

Unnamed: 0  user-0  user-1  user-2  user-3  user-4  user-5  user-6  user-7  \
0           0     4.6     0.0     0.0     0.0     4.4     4.5     4.5     0.0   
1           1     0.0     0.0     0.0     4.6     0.0     0.0     0.0     4.6   
2           2     0.0     4.6     0.0     0.0     0.0     0.0     0.0     0.0   
3           3     0.0     0.0     4.1     4.1     0.0     0.0     0.0     4.4   
4           4     4.5     4.5     4.5     4.5     4.1     0.0     0.0     4.5   

   user-8  ...  user-491  user-492  user-493  user-494  user-495  user-496  \
0     0.0  ...       4.8       0.0       4.4       0.0       0.0       4.5   
1     4.6  ...       0.0       4.7       0.0       0.0       0.0       4.7   
2     4.0  ...       0.0       0.0       0.0       0.0       0.0       0.0   
3     0.0  ...       0.0       0.0       0.0       4.3       4.6       4.0   
4     0.0  ...       0.0       0.0       4.1       4.3       4.5       4.5   

   user-497  user-498  user-499  user-500  
0       0.0       0.0       0.0       4.9  
1       4.7       4.5       4.2       0.0  
2       0.0       4.0       0.0       0.0  
3       0.0       4.1       4.3       4.2  
4       4.4       0.0       4.2       0.0  

[5 rows x 502 columns]

In [8]:
ratings.drop(['Unnamed: 0'],axis=1, inplace=True)

In [9]:
wine.insert(0,'wine_id',wine.index+1)
ratings.insert(0,'wine_id',ratings.index+1)

In [10]:
#going to use pd.melt() to to massage both DataFrames into a format where one or more columns are identifier variables, while all other columns, considered measured variables, are unpivoted to the row axis, leaving just two non-identifier columns, variable and value.
wine_1 = pd.melt(wine,id_vars=['wine_label'],var_name="wine_style",value_name="wine_id")

In [11]:
wine_1.head(100)

wine_label wine_style  wine_id
0                             Cabernet Sauvignon N.V.    wine_id      1.0
1                                   The Prisoner N.V.    wine_id      2.0
2   Costasera Amarone della Valpolicella Classico ...    wine_id      3.0
3                     ARTEMIS Cabernet Sauvignon N.V.    wine_id      4.0
4                         Brunello di Montalcino N.V.    wine_id      5.0
5                                       Opus One N.V.    wine_id      6.0
6                                    Valbuena 5º N.V.    wine_id      7.0
7                          Rouge (Gaston Hochar) N.V.    wine_id      8.0
8                               Ribera del Duero N.V.    wine_id      9.0
9                 Napa Valley Cabernet Sauvignon N.V.    wine_id     10.0
10                                          Toro N.V.    wine_id     11.0
11                                      Almaviva N.V.    wine_id     12.0
12                                       Crianza N.V.    wine_id     13.0
13                        Brunello di Montalcino N.V.    wine_id     14.0
14                         Viña Tondonia Reserva N.V.    wine_id     15.0
15                      Pèppoli Chianti Classico N.V.    wine_id     16.0
16                                           PSI N.V.    wine_id     17.0
17                               Cos d'Estournel N.V.    wine_id     18.0
18                            Cabernet Sauvignon N.V.    wine_id     19.0
19                                    Barbaresco N.V.    wine_id     20.0
20         Clark & Telephone Vineyard Pinot Noir N.V.    wine_id     21.0
21           Alexander Valley Cabernet Sauvignon N.V.    wine_id     22.0
22                                       Reserva N.V.    wine_id     23.0
23                                     Le Difese N.V.    wine_id     24.0
24            Selección Especial Sardon de Duero N.V.    wine_id     25.0
25  Península de Setúbal Quinta da Bacalhôa Cabern...    wine_id     26.0
26                  Selección Especial (Reserva) N.V.    wine_id     27.0
27                                         Tinto N.V.    wine_id     28.0
28               Las Alturas Vineyard Pinot Noir N.V.    wine_id     29.0
29                            Cabernet Sauvignon N.V.    wine_id     30.0
30                         Reserva Vinhas Velhas N.V.    wine_id     31.0
31                            Camins del Priorat N.V.    wine_id     32.0
32                  Bramare Malbec Lujan de Cuyo N.V.    wine_id     33.0
33      Abstract (a.k.a. Vandalism is Beautiful) N.V.    wine_id     34.0
34                            Cabernet Sauvignon N.V.    wine_id     35.0
35      Tenuta Guado al Tasso Bolgheri Superiore N.V.    wine_id     36.0
36                     Allomi Cabernet Sauvignon N.V.    wine_id     37.0
37                     Bin 389 Cabernet - Shiraz N.V.    wine_id     38.0
38                                        Malbec N.V.    wine_id     39.0
39                                      Insignia N.V.    wine_id     40.0
40                                Flor de Pingus N.V.    wine_id     41.0
41                            Cabernet Sauvignon N.V.    wine_id     42.0
42       Villa Antinori Chianti Classico Riserva N.V.    wine_id     43.0
43                              Pêra-Manca Tinto N.V.    wine_id     44.0
44                Napa Valley Cabernet Sauvignon N.V.    wine_id     45.0
45           Amarone della Valpolicella Classico N.V.    wine_id     46.0
46                         Bin 28 Kalimna Shiraz N.V.    wine_id     47.0
47                              The Boxer Shiraz N.V.    wine_id     48.0
48                                       Reserva N.V.    wine_id     49.0
49          Cabernet Sauvignon (Calistoga Cuvée) N.V.    wine_id     50.0
50                                      Papillon N.V.    wine_id     51.0
51                            Cabernet Sauvignon N.V.    wine_id     52.0
52                                 Rioja Reserva N.V.    wine_id     53.0
53                                       Quimer

In [12]:
ratings_1=pd.melt(ratings,id_vars=['wine_id'], var_name='user',value_name="rating")

In [13]:
ratings_1.head()

wine_id    user  rating
0        1  user-0     4.6
1        2  user-0     0.0
2        3  user-0     0.0
3        4  user-0     0.0
4        5  user-0     4.5

#### CONSTRUCT THE PIVOT TABLE

In [14]:
reco_1 = pd.merge(wine_1, ratings_1, on='wine_id')
reco_1.shape

C:\Users\tonyb\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\reshape\merge.py:1089: UserWarning: You are merging on int and float columns where the float values are not equal to their int representation
  UserWarning,


(18508944, 5)

In [15]:
reco_1.head()

wine_label wine_style  wine_id    user  rating
0  Cabernet Sauvignon N.V.    wine_id      1.0  user-0     4.6
1  Cabernet Sauvignon N.V.    wine_id      1.0  user-1     0.0
2  Cabernet Sauvignon N.V.    wine_id      1.0  user-2     0.0
3  Cabernet Sauvignon N.V.    wine_id      1.0  user-3     0.0
4  Cabernet Sauvignon N.V.    wine_id      1.0  user-4     4.4

In [16]:
pivot = pd.pivot_table(reco_1, index='wine_label', columns='user', values='rating')
pivot.head()

user                                         user-0  user-1  user-10  \
wine_label                                                             
#42 Meritage Red Blend 2016                  3.9000   3.900    3.500   
'61 Franciacorta Nature 2010                 0.4875   0.525    0.475   
'Giulio Ferrari' Riserva del Fondatore 1993  2.3000   0.000    4.675   
'Giulio Ferrari' Riserva del Fondatore 1997  3.4500   2.325    4.650   
'Giulio Ferrari' Riserva del Fondatore 2004  2.2750   3.400    2.100   

user                                         user-100  user-101  user-102  \
wine_label                                                                  
#42 Meritage Red Blend 2016                    0.0000     0.000    0.0000   
'61 Franciacorta Nature 2010                   3.5875     1.550    3.6125   
'Giulio Ferrari' Riserva del Fondatore 1993    3.4000     0.000    2.1500   
'Giulio Ferrari' Riserva del Fondatore 1997    3.4500     2.250    2.2250   
'Giulio Ferrari' Riserva del Fondatore 2004    3.3750     2.125    2.2250   

user                                         user-103  user-104  user-105  \
wine_label                                                                  
#42 Meritage Red Blend 2016                    0.0000     3.400    3.4000   
'61 Franciacorta Nature 2010                   1.0375     3.125    2.9875   
'Giulio Ferrari' Riserva del Fondatore 1993    3.4250     3.500    2.1750   
'Giulio Ferrari' Riserva del Fondatore 1997    1.2250     3.550    2.3750   
'Giulio Ferrari' Riserva del Fondatore 2004    1.1250     2.250    2.3000   

user                                         user-106  ...  user-90  user-91  \
wine_label                                             ...                     
#42 Meritage Red Blend 2016                    3.7000  ...    0.000   3.6000   
'61 Franciacorta Nature 2010                   4.1125  ...    3.725   3.8375   
'Giulio Ferrari' Riserva del Fondatore 1993    2.3000  ...    1.150   3.5750   
'Giulio Ferrari' Riserva del Fondatore 1997    3.3250  ...    2.375   2.2000   
'Giulio Ferrari' Riserva del Fondatore 2004    2.3250  ...    1.075   2.3000   

user                                         user-92  user-93  user-94  \
wine_label                                                               
#42 Meritage Red Blend 2016                    3.700   3.6000   3.8000   
'61 Franciacorta Nature 2010                   1.000   1.9875   1.0375   
'Giulio Ferrari' Riserva del Fondatore 1993    1.225   1.1250   3.4000   
'Giulio Ferrari' Riserva del Fondatore 1997    3.450   1.1500   4.6750   
'Giulio Ferrari' Riserva del Fondatore 2004    2.250   1.1000   3.2250   

user                                         user-95  user-96  user-97  \
wine_label                                                               
#42 Meritage Red Blend 2016                    3.500    3.700   3.7000   
'61 Franciacorta Nature 2010                   0.975    0.975   0.4625   
'Giulio Ferrari' Riserva del Fondatore 1993    2.250    2.225   3.5750   
'Giulio Ferrari' Riserva del Fondatore 1997    4.575    2.250   3.5000   
'Giulio Ferrari' Riserva del Fondatore 2004    1.100    3.475   2.2500   

user                                         user-98  user-99  
wine_label                                                     
#42 Meritage Red Blend 2016                   0.0000   3.8000  
'61 Franciacorta Nature 2010                  1.0125   1.5125  
'Giulio Ferrari' Riserva del Fondatore 1993   2.3750   1.1500  
'Giulio Ferrari' Riserva del Fondatore 1997   4.5750   4.4250  
'Giulio Ferrari' Riserva del Fondatore 2004   2.1000   3.2750  

[5 rows x 501 columns]

In [17]:
pivot.shape

(10450, 501)

#### CREATE THE SPARSE MATRIX

In [18]:
sparse_pivot=sparse.csr_matrix(pivot.fillna(0.0))

In [19]:
print(sparse_pivot)

  (0, 0)	3.9
  (0, 1)	3.9
  (0, 2)	3.5
  (0, 7)	3.4
  (0, 8)	3.4
  (0, 9)	3.7
  (0, 12)	3.5
  (0, 13)	3.3
  (0, 14)	3.8
  (0, 15)	3.9
  (0, 16)	3.8
  (0, 17)	3.8
  (0, 18)	3.7
  (0, 19)	3.3
  (0, 22)	3.4
  (0, 24)	3.7
  (0, 26)	3.6
  (0, 28)	3.8
  (0, 31)	3.8
  (0, 33)	3.7
  (0, 36)	3.6
  (0, 37)	3.5
  (0, 40)	3.8
  (0, 41)	3.4
  (0, 45)	3.6
  :	:
  (10449, 475)	0.975
  (10449, 476)	1.85
  (10449, 477)	2.9000000000000004
  (10449, 478)	2.0
  (10449, 479)	1.925
  (10449, 480)	1.85
  (10449, 481)	1.9749999999999999
  (10449, 482)	2.85
  (10449, 483)	2.9749999999999996
  (10449, 484)	2.0
  (10449, 485)	0.925
  (10449, 486)	0.9
  (10449, 487)	0.95
  (10449, 488)	0.975
  (10449, 489)	1.05
  (10449, 490)	2.95
  (10449, 491)	1.9
  (10449, 492)	2.05
  (10449, 493)	1.05
  (10449, 494)	2.875
  (10449, 495)	3.05
  (10449, 496)	1.95
  (10449, 498)	2.9749999999999996
  (10449, 499)	2.0
  (10449, 500)	1.9


#### CALCULATE COSINE SIMILARITY

In [20]:
recommender = pairwise_distances(sparse_pivot, metric='cosine')

#### BUILD THE RECOMMENDER

In [42]:
recommender_df = pd.DataFrame(recommender, columns=pivot.index, index=pivot.index)
recommender_df.head()

wine_label                                   #42 Meritage Red Blend 2016  \
wine_label                                                                 
#42 Meritage Red Blend 2016                                     0.000000   
'61 Franciacorta Nature 2010                                    0.369044   
'Giulio Ferrari' Riserva del Fondatore 1993                     0.346840   
'Giulio Ferrari' Riserva del Fondatore 1997                     0.349290   
'Giulio Ferrari' Riserva del Fondatore 2004                     0.363092   

wine_label                                   '61 Franciacorta Nature 2010  \
wine_label                                                                  
#42 Meritage Red Blend 2016                                      0.369044   
'61 Franciacorta Nature 2010                                     0.000000   
'Giulio Ferrari' Riserva del Fondatore 1993                      0.214066   
'Giulio Ferrari' Riserva del Fondatore 1997                      0.236213   
'Giulio Ferrari' Riserva del Fondatore 2004                      0.225844   

wine_label                                   'Giulio Ferrari' Riserva del Fondatore 1993  \
wine_label                                                                                 
#42 Meritage Red Blend 2016                                                     0.346840   
'61 Franciacorta Nature 2010                                                    0.214066   
'Giulio Ferrari' Riserva del Fondatore 1993                                     0.000000   
'Giulio Ferrari' Riserva del Fondatore 1997                                     0.195408   
'Giulio Ferrari' Riserva del Fondatore 2004                                     0.193307   

wine_label                                   'Giulio Ferrari' Riserva del Fondatore 1997  \
wine_label                                                                                 
#42 Meritage Red Blend 2016                                                     0.349290   
'61 Franciacorta Nature 2010                                                    0.236213   
'Giulio Ferrari' Riserva del Fondatore 1993                                     0.195408   
'Giulio Ferrari' Riserva del Fondatore 1997                                     0.000000   
'Giulio Ferrari' Riserva del Fondatore 2004                                     0.210387   

wine_label                                   'Giulio Ferrari' Riserva del Fondatore 2004  \
wine_label                                                                                 
#42 Meritage Red Blend 2016                                                     0.363092   
'61 Franciacorta Nature 2010                                                    0.225844   
'Giulio Ferrari' Riserva del Fondatore 1993                                     0.193307   
'Giulio Ferrari' Riserva del Fondatore 1997                                     0.210387   
'Giulio Ferrari' Riserva del Fondatore 2004                                     0.000000   

wine_label                                   'Giulio Ferrari' Riserva del Fondatore 2005  \
wine_label                                                                                 
#42 Meritage Red Blend 2016                                                     0.366439   
'61 Franciacorta Nature 2010                                                    0.216568   
'Giulio Ferrari' Riserva del Fondatore 1993                                     0.226223   
'Giulio Ferrari' Riserva del Fondatore 1997                                     0.218108   
'Giulio Ferrari' Riserva del Fondatore 2004                                     0.223368   

wine_label                                   'Giulio Ferrari' Riserva del Fondatore 2006  \
wine_label                                                                                 
#42 Meritage Red Blend 2016                                                     0.350321   
'61 Franciacorta Nature 2010                                           

In [43]:
## TEST THE RECOMMENDER

In [33]:
search = 'Rosso & Bianco'

for wine_label in wine.loc[wine['wine_label'].str.contains(search), 'wine_label']:
    print(' ')
    print('Average rating', pivot.loc[wine_label, :].mean())
    print('Number of ratings', pivot.T[wine_label].count())
    print('')
    print('10 closest wine labels')
    print('')
    print(recommender_df[wine_label].sort_values()[1:11])
    print('')
    print('*******************************************************************************************')
    print('')

 
Average rating 1.76706586826347
Number of ratings 501

10 closest wine labels

wine_label
Brut Rosé Champagne N.V.                                               0.295952
Minéral Blanc de Blancs Extra Brut Champagne Grand Cru 'Avize' 2008    0.297862
Jayson Red 2016                                                        0.298941
Châteauneuf-du-Pape Cuvée Mourre des Perdrix N.V.                      0.298962
Francs - Côtes de Bordeaux Blanc 2015                                  0.299165
Viognier 2016                                                          0.299617
Spécial Club Brut Champagne 2008                                       0.300101
Single Vineyard I Comunali Amarone della Valpolicella Classico 2014    0.300910
La Malvar de Más Que Vinos Blanco Barrica 2016                         0.301115
Pinot Noir 2016                                                        0.301181
Name: 'Rosso & Bianco' Bianco (Pinot Grigio) 2017, dtype: float64

*****************************************

In [36]:
search = 'Reserva Tempranillo 2014'

for wine_label in wine.loc[wine['wine_label'].str.contains(search), 'wine_label']:
    print(' ')
    print('Average rating', pivot.loc[wine_label, :].mean())
    print('Number of ratings', pivot.T[wine_label].count())
    print('')
    print('10 closest wine labels')
    print('')
    print(recommender_df[wine_label].sort_values()[1:11])
    print('')
    print('*******************************************************************************************')
    print('')

 
Average rating 1.8672654690618748
Number of ratings 501

10 closest wine labels

wine_label
Pinot Noir N.V.            0.285418
Sauvignon Blanc N.V.       0.285904
Chardonnay 2017            0.286087
Sauvignon Blanc 2016       0.286757
Prosecco N.V.              0.287196
Riesling 2013              0.287238
Cabernet Sauvignon 2017    0.287719
Brut Champagne 2008        0.287879
Chardonnay 2013            0.288006
Pinot Grigio 2018          0.288175
Name: Reserva Tempranillo 2014, dtype: float64

*******************************************************************************************



In [39]:
search = 'Napa Valley Cabernet Sauvignon'

for wine_label in wine.loc[wine['wine_label'].str.contains(search), 'wine_label']:
    print(' ')
    print('Average rating', pivot.loc[wine_label, :].mean())
    print('Number of ratings', pivot.T[wine_label].count())
    print('')
    print('10 closest wine labels')
    print('')
    print(recommender_df[wine_label].sort_values()[1:11])
    print('')
    print('*******************************************************************************************')
    print('')

 
Average rating 2.1066690149113554
Number of ratings 501

10 closest wine labels

wine_label
Brut Rosé Champagne N.V.                                0.030306
Prosecco N.V.                                           0.030395
O.R. 1735 Brut Champagne 2004                           0.030814
Cuvée Perle d'Ayala Millésimé Brut Aÿ Champagne 2002    0.030895
Moscato d'Asti N.V.                                     0.031412
Cuvée Joséphine Brut Champagne 2008                     0.031850
Cabernet Sauvignon N.V.                                 0.031853
Vértice Pinot Noir N.V.                                 0.032159
Chardonnay N.V.                                         0.032244
Cava Celler Batlle Gran Reserva Brut 2005               0.032273
Name: Napa Valley Cabernet Sauvignon N.V., dtype: float64

*******************************************************************************************

 
Average rating 2.1066690149113554
Number of ratings 501

10 closest wine labels

wine_label
Brut Rosé 